<a href="https://colab.research.google.com/github/ATelders/data_augmentation/blob/main/Copy_of_AugLy_audio.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Note: restart runtime after this import before running the augmentations
!pip install -U augly
!sudo apt-get install python3-magic

     |████████████████████████████████| 40.1MB 71kB/s 
     |████████████████████████████████| 61kB 6.3MB/s 
     |████████████████████████████████| 399kB 36.2MB/s 
     |████████████████████████████████| 61kB 6.0MB/s 
     |████████████████████████████████| 727kB 45.1MB/s 
     |████████████████████████████████| 112kB 47.9MB/s 
     |████████████████████████████████| 1.9MB 36.8MB/s 
     |████████████████████████████████| 51.0MB 55kB/s 
     |████████████████████████████████| 3.0MB 31.8MB/s 
     |████████████████████████████████| 27.4MB 114kB/s 
     |████████████████████████████████| 11.6MB 21.7MB/s 
     |████████████████████████████████| 645kB 32.2MB/s 
     |████████████████████████████████| 3.2MB 28.2MB/s 
     |████████████████████████████████| 3.4MB 29.0MB/s 
     |████████████████████████████████| 153kB 45.0MB/s 
     |████████████████████████████████| 184kB 46.4MB/s 
     |████████████████████████████████| 81kB 9.4MB/s 
     |████████████████████████████████| 430kB 54.1MB/s 

Reading package lists... Done
Building dependency tree       
Reading state information... Done
The following additional packages will be installed:
  libmagic-mgc libmagic1
Suggested packages:
  file
The following NEW packages will be installed:
  libmagic-mgc libmagic1 python3-magic
0 upgraded, 3 newly installed, 0 to remove and 39 not upgraded.
Need to get 262 kB of archives.
After this operation, 5,257 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 libmagic-mgc amd64 1:5.32-2ubuntu0.4 [184 kB]
Get:2 http://archive.ubuntu.com/ubuntu bionic-updates/main amd64 libmagic1 amd64 1:5.32-2ubuntu0.4 [68.6 kB]
Get:3 http://archive.ubuntu.com/ubuntu bionic/main amd64 python3-magic all 2:0.4.15-1 [9,280 B]
Fetched 262 kB in 1s (405 kB/s)
debconf: unable to initialize frontend: Dialog
debconf: (No usable dialog-like program is installed, so the dialog based frontend cannot be used. at /usr/share/perl5/Debconf/FrontEnd/Dialog.pm line 76

In [2]:
import os
import augly.audio as audaugs
import augly.utils as utils
from IPython.display import display, Audio

# Get input audio
input_audio = os.path.join(
    utils.TEST_URI, "audio", "inputs", "vad-go-stereo-44100.wav"
)
display(Audio(input_audio))

In [3]:
# Now we can apply various augmentations to the audio!
aug_audio, sr = audaugs.percussive(input_audio, 100, 16)
display(Audio(aug_audio, rate=sr))

In [4]:
"""
You can optionally pass in a metadata list, to which metadata about the
augmentation will be appended, including kwargs, the durations & number of
channels of the input & output audio clips, the matching segments in the
input/output audio clips (useful in case of temporal editing), and intensity
(defined based on the kwargs for each augmentation).
"""
meta = []
aug_audio, sr = audaugs.time_stretch(
    input_audio,
    rate=0.6,
    metadata=meta,
)
display(Audio(aug_audio, rate=sr))
meta

[{'dst_duration': 1.6379138321995466,
  'dst_num_channels': 2,
  'dst_sample_rate': 44100,
  'dst_segments': [OrderedDict([('start', 0.0), ('end', 1.6379138321995466)])],
  'intensity': 16.666666666666668,
  'name': 'time_stretch',
  'output_path': None,
  'rate': 0.6,
  'src_duration': 0.9827437641723356,
  'src_num_channels': 2,
  'src_sample_rate': 44100,
  'src_segments': [OrderedDict([('start', 0.0),
                ('end', 0.9827437641723356)])]}]

In [5]:
# For all the augmentations, we have class-based definitions as well as
# functional
from augly.audio.utils import validate_and_load_audio

input_audio_arr, sr = validate_and_load_audio(input_audio)
meta = []
aug = audaugs.LowPassFilter()
aug_audio, sr = aug(input_audio_arr, sample_rate=sr, metadata=meta)
display(Audio(aug_audio, rate=sr))
meta

[{'alpha': 0.06650056607164513,
  'cutoff_hz': 500.0,
  'dst_duration': 0.9827437641723356,
  'dst_num_channels': 2,
  'dst_sample_rate': 44100,
  'dst_segments': [OrderedDict([('start', 0.0), ('end', 0.9827437641723356)])],
  'intensity': 97.5,
  'name': 'low_pass_filter',
  'output_path': None,
  'src_duration': 0.9827437641723356,
  'src_num_channels': 2,
  'src_sample_rate': 44100,
  'src_segments': [OrderedDict([('start', 0.0),
                ('end', 0.9827437641723356)])]}]

In [6]:
# You can also compose several transformations together
meta = []
aug = audaugs.Compose(
    [
        audaugs.ApplyLambda(),
        audaugs.Reverb(),
        audaugs.ChangeVolume(-5.0)
    ]
)
aug_audio, sr = aug(input_audio_arr, sample_rate=sr, metadata=meta)
display(Audio(aug_audio, rate=sr))
meta

[{'aug_function': '<lambda>',
  'dst_duration': 0.9827437641723356,
  'dst_num_channels': 2,
  'dst_sample_rate': 44100,
  'dst_segments': [OrderedDict([('start', 0.0), ('end', 0.9827437641723356)])],
  'intensity': 100.0,
  'name': 'apply_lambda',
  'output_path': None,
  'src_duration': 0.9827437641723356,
  'src_num_channels': 2,
  'src_sample_rate': 44100,
  'src_segments': [OrderedDict([('start', 0.0),
                ('end', 0.9827437641723356)])]},
 {'dst_duration': 0.9827437641723356,
  'dst_num_channels': 2,
  'dst_sample_rate': 44100,
  'dst_segments': [OrderedDict([('start', 0.0), ('end', 0.9827437641723356)])],
  'hf_damping': 50.0,
  'intensity': 50.0,
  'name': 'reverb',
  'output_path': None,
  'pre_delay': 0.0,
  'reverberance': 50.0,
  'room_scale': 100.0,
  'src_duration': 0.9827437641723356,
  'src_num_channels': 2,
  'src_sample_rate': 44100,
  'src_segments': [OrderedDict([('start', 0.0), ('end', 0.9827437641723356)])],
  'stereo_depth': 100.0,
  'wet_gain': 0.0,
 

In [ ]:
# Testez d'autres transformations: https://github.com/facebookresearch/AugLy/blob/main/augly/audio/__init__.py

In [14]:
aug_list = [
    "AddBackgroundNoise",
    "ApplyLambda",
    "ChangeVolume",
    "Clicks",
    "Clip",
    "Harmonic",
    "HighPassFilter",
    "InsertInBackground",
    "InvertChannels",
    "LowPassFilter",
    "Normalize",
    "PeakingEqualizer",
    "Percussive",
    "PitchShift",
    "Reverb",
    "Speed",
    "Tempo",
    "TimeStretch",
    "ToMono",
]

for aug_name in aug_list:
    audio = input_audio_arr.copy()
    aug = getattr(audaugs, aug_name)()
    aug_audio, sr = aug(audio, sample_rate=sr, metadata=meta)
    print(aug)
    display(Audio(aug_audio, rate=sr))
